In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

In [2]:
% ls ./dataset

dummy_submission.csv   genome_scores.csv  tags.csv  train.csv
genome_attributes.csv  movies.csv         test.csv


In [3]:
#Loading dataset
df_train_full = pd.read_csv("./dataset/train.csv")
df_test = pd.read_csv("./dataset/test.csv")
df_submission = pd.read_csv("./dataset/dummy_submission.csv")

In [4]:
df_train_full.describe()

userId       movieId        rating
count  5.264336e+06  5.264336e+06  5.264336e+06
mean   4.987450e+03  2.591271e+03  3.360108e+00
std    2.876768e+03  1.996855e+03  1.058213e+00
min    1.000000e+00  0.000000e+00  5.000000e-01
25%    2.501000e+03  1.018000e+03  3.000000e+00
50%    5.012000e+03  2.083000e+03  3.500000e+00
75%    7.472000e+03  3.696000e+03  4.000000e+00
max    9.969000e+03  8.251000e+03  5.000000e+00

In [5]:
#Splitting into test and train data
np.random.seed(5)
indices = np.random.permutation(df_train_full.shape[0])
training_idx, test_idx = indices[:int(0.85*len(df_train_full))], indices[int(0.85*len(df_train_full)):]
df_train, df_csv = df_train_full.iloc[training_idx,:], df_train_full.iloc[test_idx,:]
#Sorting for better data handling and clarity
df_train=df_train.sort_values(by=['userId','movieId']).reset_index(drop=True)
df_csv=df_csv.sort_values(by=['userId','movieId']).reset_index(drop=True)

## <u>Baseline Prediction</u>
We first remove the inheritttent bias between users and movies using a simple baseline prediction.<br>
Here we have three parameters 
miu: 1x1 
bu: users bias 10kx1 [one for each userid]
bi: movie bias 10kx1 [one for each movieid]

In [6]:
#Baseline Prediction


def minibatch(batch_no,df,batch_size):
    '''Generates the batch for mini-batch gradient descent '''
    if (batch_no+1)*batch_size > len(df):
        minibatch_indices = indices[batch_size*(batch_no)::]
    else:        
        minibatch_indices = indices[batch_size*(batch_no):batch_size*(batch_no+1)]
    X_train = df.iloc[minibatch_indices,:]
    X_train = X_train.sort_values(by=['userId','movieId']).reset_index(drop=True)
    return X_train

def loss(parameters,df):
    miu,bu,bi = parameters
    loss = 0
    for i in range(len(df)):
        userid =  df.iloc[i,0]
        movieid = df.iloc[i,1]
        rating = miu+bu[userid]+bi[movieid]
        if rating>5:
            rating = 5
        if rating<0.5:
            rating =0.5
        loss = loss + (df.iloc[i,2]-(miu+bu[userid]+bi[movieid]))**2
    loss = loss/len(df)
    return loss    
        
def Baseline_Training(step_size,lamda,Epochs,batch_size,df):
    '''Does Mini-batch Gradient descent to optimize baseline training error'''
    
    #Initialize values for bu,b'i,miu
    #Since we are given there are 10k users and 10k movie id
    bu = np.zeros(10000)
    bi = np.zeros(10000)
    #Taking initial guess of miu as average of all ratings
    miu = np.mean(df_train.iloc[:,2])
    
    num_batches = df.shape[0]//batch_size + 1
    for epoch in range(Epochs):
        for batch in range(num_batches):
            bui = []
            X = minibatch(batch,df,batch_size)
            for i in range(len(X)):
                userid =  X.iloc[i,0]
                movieid = X.iloc[i,1]
                bui.append((miu+bu[userid]+bi[movieid]))
            #Adding the regularization term
            bu[X.userId.unique()] = (1-step_size*lamda)*bu[X.userId.unique()]
            bi[X.movieId.unique()] = (1-step_size*lamda)*bi[X.movieId.unique()]
            miu = (1-step_size*lamda)*miu            
            for i in range(len(X)):
                userid =  X.iloc[i,0]
                movieid = X.iloc[i,1]            
                bu[userid] = bu[userid] + step_size*(X.iloc[i,2]-bui[i])
                bi[movieid] = bi[movieid] + step_size*(X.iloc[i,2]-bui[i])
                miu = miu + step_size*(X.iloc[i,2]-bui[i])
            print("Epoch:{} Batch:{} ------ Training Error:{}".format(epoch,batch,loss((miu,bu,bi),X)))
    return miu,bu,bi

In [20]:
np.random.seed(5)
indices = np.random.permutation(df_train.shape[0])

#Hyperparameters
step_size = 0.001
lamda_set = [0,1e-3,1e-1,1,10]
Epochs = 5
batch_size = 1024  
loss_cv = 1000
#Regularization parameter tuning
for lamda in lamda_set:
    miu,bu,bi = Baseline_Training(step_size,lamda,Epochs,batch_size,df_train)
    loss_temp = loss((miu,bu,bi),df_csv)
    if loss_temp<loss_cv:
        best_set = (miu,bu,bi)
        loss_cv = loss_temp
        Best_lamda = lamda

Epoch:0 Batch:0 ------ Training Error:1.1714682662894842
Epoch:0 Batch:1 ------ Training Error:1.0772382078925489
Epoch:0 Batch:2 ------ Training Error:1.128943907551129
Epoch:0 Batch:3 ------ Training Error:1.1245301310139657
Epoch:0 Batch:4 ------ Training Error:1.144928258097947
Epoch:0 Batch:5 ------ Training Error:1.1669420196000875
Epoch:0 Batch:6 ------ Training Error:1.0366062739375967
Epoch:0 Batch:7 ------ Training Error:1.114409418310391
Epoch:0 Batch:8 ------ Training Error:1.2069447627069727
Epoch:0 Batch:9 ------ Training Error:1.097375325530495
Epoch:0 Batch:10 ------ Training Error:1.1964960687439279
Epoch:0 Batch:11 ------ Training Error:1.058994222149106
Epoch:0 Batch:12 ------ Training Error:1.052256743388909
Epoch:0 Batch:13 ------ Training Error:1.1617518575130608
Epoch:0 Batch:14 ------ Training Error:1.171030615149507
Epoch:0 Batch:15 ------ Training Error:1.1317066328737448
Epoch:0 Batch:16 ------ Training Error:1.0618704765508342
Epoch:0 Batch:17 ------ Trainin

Epoch:0 Batch:142 ------ Training Error:1.0465919262015084
Epoch:0 Batch:143 ------ Training Error:1.0838732843329437
Epoch:0 Batch:144 ------ Training Error:1.1041697716574113
Epoch:0 Batch:145 ------ Training Error:1.1638021274172352
Epoch:0 Batch:146 ------ Training Error:1.0565678530627902
Epoch:0 Batch:147 ------ Training Error:1.074140274377174
Epoch:0 Batch:148 ------ Training Error:1.1332634641677886
Epoch:0 Batch:149 ------ Training Error:1.0922200618455205
Epoch:0 Batch:150 ------ Training Error:1.0886892978086105
Epoch:0 Batch:151 ------ Training Error:1.033706256494282
Epoch:0 Batch:152 ------ Training Error:1.0853577980686877
Epoch:0 Batch:153 ------ Training Error:0.9601984394618152
Epoch:0 Batch:154 ------ Training Error:1.1049967394949636
Epoch:0 Batch:155 ------ Training Error:0.9764465591000411
Epoch:0 Batch:156 ------ Training Error:1.0469996280900393
Epoch:0 Batch:157 ------ Training Error:1.095879906988174
Epoch:0 Batch:158 ------ Training Error:1.1029097462330886


Epoch:0 Batch:282 ------ Training Error:1.0527815031795151
Epoch:0 Batch:283 ------ Training Error:1.060743763538558
Epoch:0 Batch:284 ------ Training Error:1.0417976928205548
Epoch:0 Batch:285 ------ Training Error:1.0936139857557203
Epoch:0 Batch:286 ------ Training Error:1.0604059195884208
Epoch:0 Batch:287 ------ Training Error:1.0124891228562973
Epoch:0 Batch:288 ------ Training Error:1.0067987960290072
Epoch:0 Batch:289 ------ Training Error:1.080422670798217
Epoch:0 Batch:290 ------ Training Error:0.9705028528613058
Epoch:0 Batch:291 ------ Training Error:1.0002488026840997
Epoch:0 Batch:292 ------ Training Error:1.216628430955222
Epoch:0 Batch:293 ------ Training Error:1.027985387987741
Epoch:0 Batch:294 ------ Training Error:1.043894448192298
Epoch:0 Batch:295 ------ Training Error:1.0920132670703915
Epoch:0 Batch:296 ------ Training Error:1.111584591714324
Epoch:0 Batch:297 ------ Training Error:1.074839203739403
Epoch:0 Batch:298 ------ Training Error:1.1294476565654405
Epoc

Epoch:0 Batch:423 ------ Training Error:0.997633628374343
Epoch:0 Batch:424 ------ Training Error:1.034352451633628
Epoch:0 Batch:425 ------ Training Error:0.9803684719420569
Epoch:0 Batch:426 ------ Training Error:1.0168126971885108
Epoch:0 Batch:427 ------ Training Error:0.9938561539755864
Epoch:0 Batch:428 ------ Training Error:1.0292198712132423
Epoch:0 Batch:429 ------ Training Error:1.0648373213482085
Epoch:0 Batch:430 ------ Training Error:1.0488682506618112
Epoch:0 Batch:431 ------ Training Error:1.080703747003863
Epoch:0 Batch:432 ------ Training Error:0.9360252523400444
Epoch:0 Batch:433 ------ Training Error:1.0899305256905385
Epoch:0 Batch:434 ------ Training Error:0.9795597922668823
Epoch:0 Batch:435 ------ Training Error:1.0245770803810732
Epoch:0 Batch:436 ------ Training Error:0.9685277356488435
Epoch:0 Batch:437 ------ Training Error:1.0219460624464412
Epoch:0 Batch:438 ------ Training Error:1.0895147135000438
Epoch:0 Batch:439 ------ Training Error:0.9852562642191167


Epoch:0 Batch:563 ------ Training Error:0.9395247839265757
Epoch:0 Batch:564 ------ Training Error:1.0194384623226924
Epoch:0 Batch:565 ------ Training Error:0.9721386035736661
Epoch:0 Batch:566 ------ Training Error:1.0158716557038368
Epoch:0 Batch:567 ------ Training Error:1.0480553313295198
Epoch:0 Batch:568 ------ Training Error:1.015023344753594
Epoch:0 Batch:569 ------ Training Error:1.0346941202655089
Epoch:0 Batch:570 ------ Training Error:0.9685018806804467
Epoch:0 Batch:571 ------ Training Error:0.9446342632055278
Epoch:0 Batch:572 ------ Training Error:0.9541855412014992
Epoch:0 Batch:573 ------ Training Error:0.9876217079226158
Epoch:0 Batch:574 ------ Training Error:1.0408014162081591
Epoch:0 Batch:575 ------ Training Error:1.0235417839444514
Epoch:0 Batch:576 ------ Training Error:0.9966348849148534
Epoch:0 Batch:577 ------ Training Error:1.0323193172493421
Epoch:0 Batch:578 ------ Training Error:1.003057955476818
Epoch:0 Batch:579 ------ Training Error:1.001282013447238


...

Epoch:4 Batch:3685 ------ Training Error:1.0136839422676678
Epoch:4 Batch:3686 ------ Training Error:0.9694965984230216
Epoch:4 Batch:3687 ------ Training Error:1.0313734668398185
Epoch:4 Batch:3688 ------ Training Error:0.9965814178927742
Epoch:4 Batch:3689 ------ Training Error:1.0520398310034729
Epoch:4 Batch:3690 ------ Training Error:1.0653979671611136
Epoch:4 Batch:3691 ------ Training Error:1.0381195340253566
Epoch:4 Batch:3692 ------ Training Error:0.9705710212028428
Epoch:4 Batch:3693 ------ Training Error:1.0621419409140185
Epoch:4 Batch:3694 ------ Training Error:1.0240083538637712
Epoch:4 Batch:3695 ------ Training Error:1.0088061177998342
Epoch:4 Batch:3696 ------ Training Error:1.0533692189464088
Epoch:4 Batch:3697 ------ Training Error:1.1423796377612887
Epoch:4 Batch:3698 ------ Training Error:1.0290642417877462
Epoch:4 Batch:3699 ------ Training Error:1.129783170960207
Epoch:4 Batch:3700 ------ Training Error:0.9786817262330455
Epoch:4 Batch:3701 ------ Training Error:

Epoch:4 Batch:3824 ------ Training Error:0.9961730065031432
Epoch:4 Batch:3825 ------ Training Error:0.9550654397396656
Epoch:4 Batch:3826 ------ Training Error:1.0345501145674507
Epoch:4 Batch:3827 ------ Training Error:0.9739086611778698
Epoch:4 Batch:3828 ------ Training Error:1.040438757996529
Epoch:4 Batch:3829 ------ Training Error:0.9792574187287153
Epoch:4 Batch:3830 ------ Training Error:0.9827579339055141
Epoch:4 Batch:3831 ------ Training Error:1.0283288419728545
Epoch:4 Batch:3832 ------ Training Error:0.9866618566325039
Epoch:4 Batch:3833 ------ Training Error:1.0247168288891422
Epoch:4 Batch:3834 ------ Training Error:0.9779705848418977
Epoch:4 Batch:3835 ------ Training Error:0.962551599748046
Epoch:4 Batch:3836 ------ Training Error:1.0742834068408949
Epoch:4 Batch:3837 ------ Training Error:0.9983739892869395
Epoch:4 Batch:3838 ------ Training Error:0.9559132235257163
Epoch:4 Batch:3839 ------ Training Error:1.0323436140125473
Epoch:4 Batch:3840 ------ Training Error:1

Epoch:4 Batch:3962 ------ Training Error:0.9845204245385689
Epoch:4 Batch:3963 ------ Training Error:0.989037932801631
Epoch:4 Batch:3964 ------ Training Error:1.0317692631305369
Epoch:4 Batch:3965 ------ Training Error:1.0833626710767514
Epoch:4 Batch:3966 ------ Training Error:0.9928953699756168
Epoch:4 Batch:3967 ------ Training Error:1.022223790081515
Epoch:4 Batch:3968 ------ Training Error:1.0246981826951107
Epoch:4 Batch:3969 ------ Training Error:1.0317400642581962
Epoch:4 Batch:3970 ------ Training Error:0.957576921117548
Epoch:4 Batch:3971 ------ Training Error:0.9711946678396608
Epoch:4 Batch:3972 ------ Training Error:1.0139639452293858
Epoch:4 Batch:3973 ------ Training Error:0.9547666866370451
Epoch:4 Batch:3974 ------ Training Error:1.0683140310733652
Epoch:4 Batch:3975 ------ Training Error:1.0411335492493978
Epoch:4 Batch:3976 ------ Training Error:0.962807980649286
Epoch:4 Batch:3977 ------ Training Error:1.0850408814845742
Epoch:4 Batch:3978 ------ Training Error:1.0

Epoch:4 Batch:4100 ------ Training Error:1.0847560112030876
Epoch:4 Batch:4101 ------ Training Error:1.0747237026400696
Epoch:4 Batch:4102 ------ Training Error:1.068036163104797
Epoch:4 Batch:4103 ------ Training Error:0.9467655456653563
Epoch:4 Batch:4104 ------ Training Error:1.1004147839677694
Epoch:4 Batch:4105 ------ Training Error:1.0600041581246133
Epoch:4 Batch:4106 ------ Training Error:0.9933195162193492
Epoch:4 Batch:4107 ------ Training Error:1.089673895232252
Epoch:4 Batch:4108 ------ Training Error:1.019195235075678
Epoch:4 Batch:4109 ------ Training Error:1.0210759268126404
Epoch:4 Batch:4110 ------ Training Error:0.951690579555596
Epoch:4 Batch:4111 ------ Training Error:1.0117250776529592
Epoch:4 Batch:4112 ------ Training Error:1.044029072188662
Epoch:4 Batch:4113 ------ Training Error:0.9325689315534109
Epoch:4 Batch:4114 ------ Training Error:1.0299431647060366
Epoch:4 Batch:4115 ------ Training Error:1.0249186508158403
Epoch:4 Batch:4116 ------ Training Error:0.95

Epoch:4 Batch:4239 ------ Training Error:0.9940493091652352
Epoch:4 Batch:4240 ------ Training Error:1.071951177890168
Epoch:4 Batch:4241 ------ Training Error:1.0302462782558952
Epoch:4 Batch:4242 ------ Training Error:1.0182268164183792
Epoch:4 Batch:4243 ------ Training Error:1.0443060940526208
Epoch:4 Batch:4244 ------ Training Error:1.064033183419492
Epoch:4 Batch:4245 ------ Training Error:0.9806619310487812
Epoch:4 Batch:4246 ------ Training Error:1.0797789446066657
Epoch:4 Batch:4247 ------ Training Error:1.0161880295744532
Epoch:4 Batch:4248 ------ Training Error:0.9576931812909387
Epoch:4 Batch:4249 ------ Training Error:1.1566982804778305
Epoch:4 Batch:4250 ------ Training Error:1.0475221125192513
Epoch:4 Batch:4251 ------ Training Error:1.0628823182189182
Epoch:4 Batch:4252 ------ Training Error:1.0857525932703416
Epoch:4 Batch:4253 ------ Training Error:1.0458347548731046
Epoch:4 Batch:4254 ------ Training Error:0.9995987157169915
Epoch:4 Batch:4255 ------ Training Error:1

In [ ]:
np.random.seed(5)
indices = np.random.permutation(df_train.shape[0])

#Hyperparameters
step_size = 0.001
lamda_set = 0
Epochs = 20
batch_size = 1024  



In [22]:
import pickle
with open('data.pickle', 'wb') as f:
    pickle.dump(best_set, f)

In [ ]:
print('Final Training Loss:{} \n Final Test set loss:{}'.format(loss((miu,bu,bi),df_train),loss((miu,bu,bi),df_csv)))

In [209]:
#Submission
predictions = np.zeros(len(df_test))
for i in range(len(df_test)):
    userid =  df_test.iloc[i,0]
    movieid = df_test.iloc[i,1]
    rating = float("{0:.1f}".format(miu+bu[userid]+bi[movieid]))
    if rating>5:
        rating = 5
    if rating<0.5:
        rating =0.5
    predictions[i] = rating
df_submission.Prediction = predictions
df_submission.to_csv('./Submission.csv',index=False)